Необходимо собрать информацию о вакансиях на вводимую должность (используем input или через аргументы) с сайтов Superjob и HH. Приложение должно анализировать несколько страниц сайта (также вводим через input или аргументы). Получившийся список должен содержать в себе минимум:
Наименование вакансии.
Предлагаемую зарплату (отдельно минимальную и максимальную).
Ссылку на саму вакансию.
Сайт, откуда собрана вакансия. ### По желанию можно добавить ещё параметры вакансии (например, работодателя и расположение). Структура должна быть одинаковая для вакансий с обоих сайтов. Общий результат можно вывести с помощью dataFrame через pandas.

In [598]:
from bs4 import BeautifulSoup as bs  
from bs4 import BeautifulStoneSoup    
import bs4     
import requests
import json
import pandas as pd
import numpy as np
import re

**Решение через API**

In [599]:
def getPage(page = 0):
    """
    Создаем метод для получения страницы со списком вакансий.
    Аргументы:
        page - Индекс страницы, начинается с 0. Значение по умолчанию 0, т.е. первая страница
    """
     
    # Справочник для параметров GET-запроса
    params = {
        'text': 'NAME:Data Scientist', # Текст фильтра. В имени должно быть слово "Аналитик"
        'area': 1, # Поиск ощуществляется по вакансиям города Москва
        'page': page, # Индекс страницы поиска на HH
        'per_page': 100 # Кол-во вакансий на 1 странице
    }
     
     
    req = requests.get('https://api.hh.ru/vacancies', params) # Посылаем запрос к API
    data = req.content.decode() # Декодируем его ответ, чтобы Кириллица отображалась корректно
    req.close()
    return data

In [600]:
jsObj = json.loads(getPage(0))
my_df = pd.DataFrame.from_dict(jsObj['items'], orient='columns')
# Считываем первые 2000 вакансий
for page in range(1, 20):
     
    # Преобразуем текст ответа запроса в справочник Python
    jsObj = json.loads(getPage(page))
    my_df_ = pd.DataFrame.from_dict(jsObj['items'], orient='columns')
    my_df = pd.concat([my_df, my_df_], axis=0)
    # Проверка на последнюю страницу, если вакансий меньше 2000
    if (jsObj['pages'] - page) <= 1:
        break
     
print('Старницы поиска собраны')

Старницы поиска собраны


In [601]:
my_df.head(2)

id  premium            name department  has_test  \
0  48434078    False  Data Scientist       None     False   
1  48612849    False  Data scientist       None     False   

   response_letter_required  \
0                     False   
1                     False   

                                                area  \
0  {'id': '1', 'name': 'Москва', 'url': 'https://...   
1  {'id': '1', 'name': 'Москва', 'url': 'https://...   

                                              salary  \
0  {'from': 180000, 'to': 250000, 'currency': 'RU...   
1  {'from': 400000, 'to': None, 'currency': 'RUR'...   

                                 type  \
0  {'id': 'open', 'name': 'Открытая'}   
1  {'id': 'open', 'name': 'Открытая'}   

                                             address  ...  \
0                                               None  ...   
1  {'city': 'Москва', 'street': '17-й проезд Марь...  ...   

                    alternate_url relations  \
0  https://hh.ru/vacancy/48434078        []   
1  https://hh.ru/vacancy/48612849        []   

                                            employer  \
0  {'id': '1664868', 'name': 'CORE', 'url': 'http...   
1  {'id': '1939023', 'name': 'Премьер Аналитика',...   

                                             snippet  contacts  \
0  {'requirement': 'Знание и опыт применения клас...      None   
1  {'requirement': 'Понимание технологий ML, AI. ...      None   

                                       schedule working_days  \
0  {'id': 'remote', 'name': 'Удаленная работа'}           []   
1      {'id': 'fullDay', 'name': 'Полный день'}           []   

  working_time_intervals working_time_modes accept_temporary  
0                     []                 []            False  
1                     []                 []            False  

[2 rows x 28 columns]

In [602]:
my_df.set_index('id', inplace=True)

In [603]:
my_df.sample(6)

premium                                name department  has_test  \
id                                                                           
48164825    False          ML Engineer/Data Scientist       None     False   
48285387    False   ML Engineer/ Data Scientist (WAF)       None     False   
47791818    False  Middle/Senior Data Scientist (NLP)       None     False   
48654914    False   Senior data scientist (Team Lead)       None     False   
48102976    False                      Data Scientist       None     False   
48019248    False               Senior Data Scientist       None     False   

          response_letter_required  \
id                                   
48164825                     False   
48285387                     False   
47791818                     False   
48654914                     False   
48102976                     False   
48019248                     False   

                                                       area  \
id                                                            
48164825  {'id': '1', 'name': 'Москва', 'url': 'https://...   
48285387  {'id': '1', 'name': 'Москва', 'url': 'https://...   
47791818  {'id': '1', 'name': 'Москва', 'url': 'https://...   
48654914  {'id': '1', 'name': 'Москва', 'url': 'https://...   
48102976  {'id': '1', 'name': 'Москва', 'url': 'https://...   
48019248  {'id': '1', 'name': 'Москва', 'url': 'https://...   

                                                     salary  \
id                                                            
48164825  {'from': 160000, 'to': 220000, 'currency': 'RU...   
48285387                                               None   
47791818                                               None   
48654914                                               None   
48102976  {'from': None, 'to': 250000, 'currency': 'RUR'...   
48019248                                               None   

                                        type  \
id                                             
48164825  {'id': 'open', 'name': 'Открытая'}   
48285387  {'id': 'open', 'name': 'Открытая'}   
47791818  {'id': 'open', 'name': 'Открытая'}   
48654914  {'id': 'open', 'name': 'Открытая'}   
48102976  {'id': 'open', 'name': 'Открытая'}   
48019248  {'id': 'open', 'name': 'Открытая'}   

                                                    address response_url  ...  \
id                                                                        ...   
48164825  {'city': 'Москва', 'street': 'Западный админис...         None  ...   
48285387  {'city': 'Москва', 'street': 'Преображенская п...         None  ...   
47791818  {'city': 'Москва', 'street': 'улица Земляной В...         None  ...   
48654914  {'city': 'Москва', 'street': 'Краснопролетарск...         None  ...   
48102976                                               None         None  ...   
48019248  {'city': 'Москва', 'street': 'Денисовский пере...         None  ...   

                           alternate_url relations  \
id                                                   
48164825  https://hh.ru/vacancy/48164825        []   
48285387  https://hh.ru/vacancy/48285387        []   
47791818  https://hh.ru/vacancy/47791818        []   
48654914  https://hh.ru/vacancy/48654914        []   
48102976  https://hh.ru/vacancy/48102976        []   
48019248  https://hh.ru/vacancy/48019248        []   

                                                   employer  \
id                                                            
48164825  {'id': '5728483', 'name': 'Газарова Екатерина'...   
48285387  {'id': '26624', 'name': 'Positive Technologies...   
47791818  {'id': '4585', 'name': 'ЦРТ | Группа компаний'...   
48654914  {'id': '4934', 'name': 'Билайн', 'url': 'https...   
48102976  {'id': '1319166', 'name': 'Экспириенс', 'url':...   
48019248  {'id': '196122', 'name': 'Teradata', 'url': 'h...   

                                                    snippet contacts  \
id                        

In [604]:
for i, row in my_df.iterrows():
    if row['salary'] != None:
        for e in row['salary']:
            my_df.loc[i, e] = row['salary'][e]

In [605]:
my_df.rename(columns={'from': 'salary_from', 'to':'salary_to', 'currency':'salary_currency', 'gross':'salary_gross'}, inplace=True)

In [606]:
# c NaN этот код отказывается работать

#temp_df = my_df['salary'] #.pop('salary')
#temp_df = pd.DataFrame.from_records(temp_df)
#temp_df

In [607]:
for i, row in my_df.iterrows():
    if row['area'] != None:
        for e in row['area']:
            my_df.loc[i, e] = row['area'][e]

In [608]:
my_df.head(2)

premium    name department  has_test  response_letter_required  \
id                                                                         
48434078    False  Москва       None     False                     False   
48612849    False  Москва       None     False                     False   

                                                       area  \
id                                                            
48434078  {'id': '1', 'name': 'Москва', 'url': 'https://...   
48612849  {'id': '1', 'name': 'Москва', 'url': 'https://...   

                                                     salary  \
id                                                            
48434078  {'from': 180000, 'to': 250000, 'currency': 'RU...   
48612849  {'from': 400000, 'to': None, 'currency': 'RUR'...   

                                        type  \
id                                             
48434078  {'id': 'open', 'name': 'Открытая'}   
48612849  {'id': 'open', 'name': 'Открытая'}   

                                                    address response_url  ...  \
id                                                                        ...   
48434078                                               None         None  ...   
48612849  {'city': 'Москва', 'street': '17-й проезд Марь...         None  ...   

                                              schedule working_days  \
id                                                                    
48434078  {'id': 'remote', 'name': 'Удаленная работа'}           []   
48612849      {'id': 'fullDay', 'name': 'Полный день'}           []   

         working_time_intervals  working_time_modes accept_temporary  \
id                                                                     
48434078                     []                  []            False   
48612849                     []                  []            False   

         salary_from salary_to salary_currency salary_gross id  
id                                                              
48434078    180000.0  250000.0             RUR        False  1  
48612849    400000.0       NaN             RUR        False  1  

[2 rows x 32 columns]

In [609]:
my_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 327 entries, 48434078 to 47821387
Data columns (total 32 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   premium                   327 non-null    bool   
 1   name                      327 non-null    object 
 2   department                103 non-null    object 
 3   has_test                  327 non-null    bool   
 4   response_letter_required  327 non-null    bool   
 5   area                      327 non-null    object 
 6   salary                    56 non-null     object 
 7   type                      327 non-null    object 
 8   address                   149 non-null    object 
 9   response_url              0 non-null      object 
 10  sort_point_distance       0 non-null      object 
 11  published_at              327 non-null    object 
 12  created_at                327 non-null    object 
 13  archived                  327 non-null    bool   
 14  app

**Решение методом тыков по странице**

In [610]:
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager

In [611]:
driver = webdriver.Chrome(ChromeDriverManager().install())



====== WebDriver manager ======
Current google-chrome version is 94.0.4606
Get LATEST driver version for 94.0.4606
Get LATEST driver version for 94.0.4606
Trying to download new driver from https://chromedriver.storage.googleapis.com/94.0.4606.61/chromedriver_win32.zip
Driver has been saved in cache [C:\Users\Андрей\.wdm\drivers\chromedriver\win32\94.0.4606.61]


In [612]:
driver.get('https://russia.superjob.ru/vakansii/')

In [613]:
source_data = driver.page_source

In [614]:
soup = bs(source_data)

In [615]:
target_name = 'data scientist'

In [617]:
#print(soup.prettify())

<html class="no-js" lang="ru">
 <head>
  <meta charset="utf-8"/>
  <meta content="ie=edge" http-equiv="x-ua-compatible"/>
  <title>
   Работа и вакансии в России
  </title>
  <meta content="SuperJob – сервис по поиску высокооплачиваемой работы. 20 лет на рынке! Огромная база зарегистрированных работодателей. Более 800 000 вакансий" name="description"/>
  <meta content="вакансии, поиск вакансий, найти вакансию, работа, найти работу, поиск работы" name="keywords"/>
  <meta content="notranslate" name="google"/>
  <meta content="6fa953a8f9" name="verify-admitad"/>
  <meta content="width=device-width" name="viewport"/>
  <meta content="telephone=no" name="format-detection"/>
  <meta content="browserconfig.xml" name="msapplication-config"/>
  <link href="/fstc/desktop/favicon.ico" rel="shortcut icon"/>
  <link href="/fstc/desktop/favicon.png" rel="icon" sizes="558x558" type="image/png"/>
  <link href="/fstc/desktop/favicon-16x16.png" rel="icon" sizes="16x16" type="image/png"/>
  <link href="

In [623]:
tag_search = soup.find_all('input')
tag_search

[<input autocomplete="off" class="daOr9 daOr9 _18QIQ f-test-input-keywords" maxlength="500" name="keywords" placeholder="Должность, компания или услуга" type="text" value=""/>]

In [621]:
sbox = driver.find_element_by_class_name("f-test-input-keywords")
sbox

<selenium.webdriver.remote.webelement.WebElement (session="6c165a9e0a5aaefbe64bcd55a5dd0851", element="f3f30770-9889-4592-a304-7bcdd84399a1")>

In [622]:
sbox.send_keys(target_name)

In [624]:
sbox.submit()

отправляем текст))

In [625]:
source_data = driver.page_source

In [626]:
soup = bs(source_data)

In [633]:
#print(soup.prettify())

<html class="no-js" lang="ru">
 <head>
  <meta charset="utf-8"/>
  <meta content="ie=edge" http-equiv="x-ua-compatible"/>
  <title>
   Data Scientist, работа Data Scientist, вакансии Data Scientist в России
  </title>
  <meta content="notranslate" name="google"/>
  <meta content="6fa953a8f9" name="verify-admitad"/>
  <meta content="width=device-width" name="viewport"/>
  <meta content="telephone=no" name="format-detection"/>
  <meta content="browserconfig.xml" name="msapplication-config"/>
  <link href="/fstc/desktop/favicon.ico" rel="shortcut icon"/>
  <link href="/fstc/desktop/favicon.png" rel="icon" sizes="558x558" type="image/png"/>
  <link href="/fstc/desktop/favicon-16x16.png" rel="icon" sizes="16x16" type="image/png"/>
  <link href="/fstc/desktop/favicon-32x32.png" rel="icon" sizes="32x32" type="image/png"/>
  <link href="/fstc/desktop/apple-touch-icon.png" rel="apple-touch-icon"/>
  <link color="#00aa87" href="/fstc/desktop/safari-pinned-tab.svg" rel="mask-icon"/>
  <link href=

In [638]:
tag_search = soup.find_all('div',attrs={'class' : re.compile("f-test-search-result-item")})
#tag_search

In [680]:
df_list = []

In [679]:
def list_app(tag_search):
    for el in tag_search:
        tree_vac = {}
        vac_url = ''
        el_name = el.find('a',attrs={'class' : re.compile("icMQ_")})
        el_salary = el.find('span',attrs={'class' : re.compile("_1OuF_")})
        el_firma = el.find('span',attrs={'class' : re.compile("_1h3Zg _3Fsn4")})
        el_sity = el.find('span',attrs={'class' : re.compile("_1h3Zg f-test-text-company-item-location")})
        try:
            print(el_name.text, ' ', el_salary.text, ' ', vac_url, ' ', el_firma.text, ' ', el_sity.text)
            vac_url = 'https://russia.superjob.ru/' + el_name.get('href')
            tree_vac['Вакансия'] = el_name.text
            tree_vac['Зарплата'] = el_salary.text
            tree_vac['Сайт'] = vac_url
            tree_vac['Работодатель'] = el_firma.text
            tree_vac['Город и время публикации'] = el_sity.text
            df_list.append(tree_vac)
        except:
            print('')

In [681]:
list_app(tag_search)

Data Scientist   По договорённости      Сбербанк России   11:15 • Екатеринбург
Middle Data Scientist   от 104 000 руб./месяц      Автоматизация и консалтинг   7 октября • Москва
ML engineer / Data scientist   По договорённости      Brightlab   6 октября • Ростов-на-Дону

Программист / Data scientist   По договорённости      ПРОИНВЕСТЛАЙН   5 октября • Москва, Новослободская
Data Scientist (Отдел аудита обеспечивающих процессов)   По договорённости      Сбербанк России   8:30 • Екатеринбург

Аналитик данных (Data Scientist)   По договорённости      Сбербанк России   6:45 • Хабаровск

Data scientist   По договорённости      Сбербанк России   Вчера • Москва, Тульская и ещё 2 станции
Senior Data Scientist   По договорённости      Сбербанк России   Вчера • Сочи

Jr. Data Scientist   По договорённости      Сбербанк России   Вчера • Екатеринбург
Senior Data Scientist   от 174 000 руб./месяц      Автоматизация и консалтинг   7 октября • Москва
Lead data analyst / Product owner (Analytics Team)

переходим по страницам до конца

In [684]:
while True:
    try:
        sbox = driver.find_element_by_class_name("f-test-button-dalshe")
        sbox.click()
        source_data = driver.page_source
        soup = bs(source_data)
        tag_search = soup.find_all('div',attrs={'class' : re.compile("f-test-search-result-item")})
        list_app(tag_search)
    except:
        break

Системный аналитик (СберИнвестор)   По договорённости      Сбербанк России   12:15 • Зеленоград
DevOps-инженер   По договорённости      BrightLab   7 октября • Ростов-на-Дону
Старший разработчик MS SQL + C#.net   до 210 000 руб./месяц      Консалтинговая компания   7 октября • Новосибирск
JavaScript (React) разработчик   до 220 000 руб./месяц      Эрис   4 октября • Омск



In [685]:
my_df_2 = pd.DataFrame(df_list)

In [948]:
my_df_2.head(5)

Вакансия               Зарплата  \
0                                     Data Scientist      По договорённости   
1                              Middle Data Scientist  от 104 000 руб./месяц   
2                       ML engineer / Data scientist      По договорённости   
3                       Программист / Data scientist      По договорённости   
4  Data Scientist (Отдел аудита обеспечивающих пр...      По договорённости   

                                                Сайт  \
0  https://russia.superjob.ru//vakansii/data-scie...   
1  https://russia.superjob.ru//vakansii/middle-da...   
2  https://russia.superjob.ru//vakansii/ml-engine...   
3  https://russia.superjob.ru//vakansii/programmi...   
4  https://russia.superjob.ru//vakansii/data-scie...   

                 Работодатель            Город и время публикации Зарплата от  \
0             Сбербанк России                11:15 • Екатеринбург         NaN   
1  Автоматизация и консалтинг                  7 октября • Москва   [104 000]   
2                   Brightlab          6 октября • Ростов-на-Дону         NaN   
3               ПРОИНВЕСТЛАЙН  5 октября • Москва, Новослободская         NaN   
4             Сбербанк России                 8:30 • Екатеринбург         NaN   

  Зарплата до  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN

In [690]:
my_df_2['Зарплата от'] = 'NaN'
my_df_2['Зарплата до'] = 'NaN'

In [895]:
my_df_2.loc[my_df_2['Зарплата'].str.match('от'), 'Зарплата от'] = my_df_2['Зарплата'].str.findall(r'(\d+.\d+)')

In [896]:
my_df_2.loc[my_df_2['Зарплата'].str.match('до'), 'Зарплата до'] = my_df_2['Зарплата'].str.findall(r'(\d+.\d+)')

In [892]:
my_df_2.loc[my_df_2['Зарплата'].str.match(r'\d'), 'Зарплата от'] = my_df_2['Зарплата'].str.findall(r'(^\d+.\d+)')

In [911]:
my_df_2.loc[my_df_2['Зарплата'].str.match(r'\d'), 'Зарплата до'] = my_df_2['Зарплата'].str.findall(r'—.(\d+.\d+)')

In [946]:
my_df_2.to_csv("./superjob.csv", index=False)

In [947]:
my_df.to_csv("./api_hh.csv", index=False)